In [1]:
import json, requests, urllib

In [2]:
import pandas as pd

In [3]:
response = requests.get("https://huggingface.co/api/models?filter=co2_eq_emissions")

In [4]:
modelcount=0
carboncount=0

carbon_df = pd.DataFrame(columns=['name','task','carbon'])

for model in response.json():
    modelcount+=1
    if model['private'] == False:
        try:
            readme = urllib.request.urlopen("https://huggingface.co/"+model['modelId']+"/raw/main/README.md")
            for line in readme:
                decoded_line = line.decode("utf-8")
                if 'co2_eq_emissions' in decoded_line:
                    carboncount+=1
                    #print(model['modelId'], model['pipeline_tag'], decoded_line.split(":")[1])
                    try:
                        carbon_df.at[carboncount,'name'] = str(model['modelId'])
                        carbon_df.at[carboncount,'task'] = str(model['pipeline_tag'])
                        carbon_df.at[carboncount,'carbon'] = float(decoded_line.split(":")[1].replace('\n',''))
                    except:
                        carbon_df.at[carboncount,'name'] = str(model['modelId'])
                        carbon_df.at[carboncount,'task'] = ''
                        carbon_df.at[carboncount,'carbon'] = float(decoded_line.split(":")[1].replace('\n',''))
        except:
            continue
print("Out of "+str(modelcount)+" models, "+str(carboncount)+ " of them reported carbon emissions")

Out of 78 models, 78 of them reported carbon emissions


In [5]:
carbon_df.head()

name                  task  \
1                    Aimendo/autonlp-triage-35248482   text-classification   
2                                     Anorak/nirvana  text2text-generation   
3  AryanLala/autonlp-Scientific_Title_Generator-3...  text2text-generation   
4                        Crasher222/kaggle-comp-test   text-classification   
5                     Emanuel/autonlp-pos-tag-bosque  token-classification   

       carbon  
1    7.989145  
2    4.214013  
3  137.605741  
4   60.744727  
5    6.210727

In [11]:
carbon_df.to_pickle("./carbon_df.pkl")